In [1]:
# from tqdm import tqdm
from tqdm.notebook import tqdm
from datasets import load_dataset, DatasetDict, load_from_disk
# from transformers import GPT2Tokenizer, GPT2Config, GPT2LMHeadModel, GPT2LMHeadModel
# from transformers import DataCollatorForLanguageModeling
from transformers import Trainer, TrainingArguments
import accelerate
import transformers
# transformers.__version__, accelerate.__version__
import torch
torch.cuda.is_available()
# from scripts.utils import *
from pathlib import Path

import sys
import os

scripts_dir = os.path.abspath(os.path.join(os.getcwd(), '..', 'scripts'))

if scripts_dir not in sys.path:
    sys.path.append(scripts_dir)

from utils import *
from candor_surprisals import main, concat_surprisals_to_full_df
from candor_final_df import make_df_from_convo_path

device = "cuda" if torch.cuda.is_available() else "cpu"
print(torch.cuda.get_device_name(0))


NVIDIA A100 80GB PCIe


In [2]:
candor_convo_path = '../data/candor/sample/0020a0c5-1658-4747-99c1-2839e736b481/'

models = {
    ('left', 'sentence'): '../models/gpt2/left_sentence/checkpoint-76066',
    ('right', 'sentence'): '../models/gpt2/right_sentence/checkpoint-76066',
    ('bidi', 'sentence'): '../models/gpt2/bidi_sentence/checkpoint-76066',
    ('left', 'bigram'): '../models/gpt2/left_bigram/checkpoint-63819',
    ('right', 'bigram'): '../models/gpt2/right_bigram/checkpoint-63819',
    ('bidi', 'bigram'): '../models/gpt2/bidi_bigram/checkpoint-100000',
}

In [3]:
all_model_surprisals = {}
for (context_direction, context_size), model_dir in models.items():
    model_surprisals = main(candor_convo_path, model_dir, context_size, context_direction)
    all_model_surprisals[(context_direction, context_size)] = model_surprisals

Loading pretrained model from ../models/gpt2/left_sentence/checkpoint-76066...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['[BOS]', '[EOS]', '<|endoftext|>']
...done



100%|██████████| 856/856 [00:06<00:00, 126.12it/s]


Loading pretrained model from ../models/gpt2/right_sentence/checkpoint-76066...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['[BOS]', '[EOS]', '<|endoftext|>']
...done



100%|██████████| 856/856 [00:06<00:00, 127.15it/s]


Loading pretrained model from ../models/gpt2/bidi_sentence/checkpoint-76066...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['[BOS]', '[EOS]', '<|endoftext|>', '[SEP]', '[FILLER]', '[BLANK]']
...done



...

100%|██████████| 7721/7721 [00:37<00:00, 206.55it/s]


Loading pretrained model from ../models/gpt2/right_bigram/checkpoint-63819...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['<s>', '</s>', '<|endoftext|>']
...done



100%|██████████| 7721/7721 [00:39<00:00, 197.36it/s]


Loading pretrained model from ../models/gpt2/bidi_bigram/checkpoint-100000...
...done

Loading pretrained tokenizer from gpt2...
Vocabulary size: 50257
Max Model Input Sizes: 1024
Special tokens: ['<s>', '</s>', '<|endoftext|>', '[SEP]', '[FILLER]', '[BLANK]']
...done



100%|██████████| 7721/7721 [00:51<00:00, 150.12it/s]


In [4]:
full_df = make_df_from_convo_path(Path(candor_convo_path))

In [9]:
full_df

turn_id    word word_start word_stop   text  lemma n_chars n_syllables  \
0           0    Mhm.       4.34      4.66    Mhm    Mhm       3           2   
1           0    Mhm.      10.14     10.95    Mhm    Mhm       3           2   
2           0   Just,      12.74     14.36   Just   just       4           1   
3           0     mm.      17.74     17.95     mm     mm       2        None   
4           0     And      18.74     19.06    And    and       3           1   
...       ...     ...        ...       ...    ...    ...     ...         ...   
7716      322    good    2732.43   2732.56   good   good       4           1   
7717      322  night.    2732.56    2733.0  night  night       5           1   
7718      323   Yeah.    2732.59   2732.79   Yeah   yeah       4           1   
7719      323   Yeah.    2733.29   2734.09   Yeah   yeah       4           1   
7720      324     But    2734.39   2734.66    But    but       3           1   

        pos stopword    mtw sentence_id_in_turn word_id_in_sentence  \
0     PROPN    False  False                   0                   0   
1     PROPN    False  False                   1                   0   
2       ADV     True  False                   2                   0   
3      INTJ    False  False                   2                   1   
4     CCONJ     True  False                   3                   0   
...     ...      ...    ...                 ...                 ...   
7716    ADJ    False  False                   1                   2   
7717   NOUN    False  False                   1                   3   
7718   INTJ    False  False                   0                   0   
7719   INTJ    False  False                   1                   0   
7720  CCONJ     True  False                   0                   0   

      position_in_turn  
0                    0  
1                    1  
2                    2  
3                    3  
4                    4  
...                ...  
7716                 5  
7717                 6  
7718                 0  
7719                 1  
7720                 0  

[7721 rows x 14 columns]

In [11]:
full_df = full_df[full_df.columns[[0, 11, 12, 13, *range(1, 11)]]]
full_df

turn_id sentence_id_in_turn word_id_in_sentence  position_in_turn  \
0           0                   0                   0                 0   
1           0                   1                   0                 1   
2           0                   2                   0                 2   
3           0                   2                   1                 3   
4           0                   3                   0                 4   
...       ...                 ...                 ...               ...   
7716      322                   1                   2                 5   
7717      322                   1                   3                 6   
7718      323                   0                   0                 0   
7719      323                   1                   0                 1   
7720      324                   0                   0                 0   

        word word_start word_stop   text  lemma n_chars n_syllables    pos  \
0       Mhm.       4.34      4.66    Mhm    Mhm       3           2  PROPN   
1       Mhm.      10.14     10.95    Mhm    Mhm       3           2  PROPN   
2      Just,      12.74     14.36   Just   just       4           1    ADV   
3        mm.      17.74     17.95     mm     mm       2        None   INTJ   
4        And      18.74     19.06    And    and       3           1  CCONJ   
...      ...        ...       ...    ...    ...     ...         ...    ...   
7716    good    2732.43   2732.56   good   good       4           1    ADJ   
7717  night.    2732.56    2733.0  night  night       5           1   NOUN   
7718   Yeah.    2732.59   2732.79   Yeah   yeah       4           1   INTJ   
7719   Yeah.    2733.29   2734.09   Yeah   yeah       4           1   INTJ   
7720     But    2734.39   2734.66    But    but       3           1  CCONJ   

     stopword    mtw  
0       False  False  
1       False  False  
2        True  False  
3       False  False  
4        True  False  
...       ...    ...  
7716    False  False  
7717    False  False  
7718    False  False  
7719    False  False  
7720     True  False  

[7721 rows x 14 columns]

In [12]:
for k, v in all_model_surprisals.items():
    print(k, len(v))

('left', 'sentence') 7721
('right', 'sentence') 7721
('bidi', 'sentence') 7721
('left', 'bigram') 7721
('right', 'bigram') 7721
('bidi', 'bigram') 7721


In [13]:
out_df = concat_surprisals_to_full_df(full_df, {'_'.join(k): v for k, v in all_model_surprisals.items()})

In [14]:
out_df

turn_id sentence_id_in_turn word_id_in_sentence  position_in_turn  \
0           0                   0                   0                 0   
1           0                   1                   0                 1   
2           0                   2                   0                 2   
3           0                   2                   1                 3   
4           0                   3                   0                 4   
...       ...                 ...                 ...               ...   
7716      322                   1                   2                 5   
7717      322                   1                   3                 6   
7718      323                   0                   0                 0   
7719      323                   1                   0                 1   
7720      324                   0                   0                 0   

        word word_start word_stop   text  lemma n_chars n_syllables    pos  \
0       Mhm.       4.34      4.66    Mhm    Mhm       3           2  PROPN   
1       Mhm.      10.14     10.95    Mhm    Mhm       3           2  PROPN   
2      Just,      12.74     14.36   Just   just       4           1    ADV   
3        mm.      17.74     17.95     mm     mm       2        None   INTJ   
4        And      18.74     19.06    And    and       3           1  CCONJ   
...      ...        ...       ...    ...    ...     ...         ...    ...   
7716    good    2732.43   2732.56   good   good       4           1    ADJ   
7717  night.    2732.56    2733.0  night  night       5           1   NOUN   
7718   Yeah.    2732.59   2732.79   Yeah   yeah       4           1   INTJ   
7719   Yeah.    2733.29   2734.09   Yeah   yeah       4           1   INTJ   
7720     But    2734.39   2734.66    But    but       3           1  CCONJ   

     stopword    mtw  left_sentence  right_sentence  bidi_sentence  \
0       False  False      14.247051       17.214086       6.310241   
1       False  False      14.247051       17.214086       6.310241   
2        True  False       9.744504       10.990050       6.055397   
3       False  False      12.407815       11.694961       6.108757   
4        True  False       2.748569       12.719169       9.426615   
...       ...    ...            ...             ...            ...   
7716    False  False       1.356899        3.564446       9.403681   
7717    False  False       2.878433        6.771707       5.927935   
7718    False  False       4.249014        3.994786       5.398063   
7719    False  False       4.249014        3.994786       5.398063   
7720     True  False       3.637504       13.285196      10.514117   

      left_bigram  right_bigram  bidi_bigram  
0       18.384441     18.408640    30.430573  
1       18.384441     18.408640    30.430573  
2        6.128322      9.310482    19.339494  
3       12.510981     12.028164    20.514782  
4        2.312116      8.054623     2.546889  
...           ...           ...          ...  
7716     4.064208      3.977333     6.232678  
7717     5.639752      6.654217    18.155780  
7718     5.594672      4.854791    18.202595  
7719     5.594672      4.854791    18.202595  
7720     3.167184     12.125416     4.100402  

[7721 rows x 20 columns]

In [19]:
import pandas as pd

In [20]:
with pd.option_context('display.max_rows', None, 'display.max_columns', None):  # more options can be specified also
    display(out_df)

turn_id sentence_id_in_turn word_id_in_sentence  position_in_turn  \
0           0                   0                   0                 0   
1           0                   1                   0                 1   
2           0                   2                   0                 2   
3           0                   2                   1                 3   
4           0                   3                   0                 4   
5           0                   3                   1                 5   
6           0                   3                   2                 6   
7           0                   3                   3                 7   
8           0                   4                   0                 8   
9           0                   5                   0                 9   
10          0                   6                   0                10   
11          0                   7                   0                11   
12          0                   8                   0                12   
13          0                   8                   1                13   
14          0                   9                   0                14   
15          0                  10                   0                15   
16          0                  11                   0                16   
17          0                  12                   0                17   
18          0                  13                   0                18   
19          0                  14                   0                19   
20          0                  15                   0                20   
21          0                  15                   1                21   
22          0                  16                   0                22   
23          0                  17                   0                23   
24          0                  18                   0                24   
25          0                  19                   0                25   
26          0                  20                   0                26   
27          0                  21                   0                27   
28          0                  22                   0                28   
29          0                  23                   0                29   
30          0                  24                   0                30   
31          0                  25                   0                31   
32          0                  26                   0                32   
33          0                  27                   0                33   
34          0                  28                   0                34   
35          0                  29                   0                35   
36          0                  30                   0                36   
37          0                  31                   0                37   
38          1                   0                   0                 0   
39          1                   0                   1                 1   
40          1                   0                   2                 2   
41          1                   0                   3                 3   
42          2                   0                   0                 0   
43          2                   0                   1                 1   
44          2                   0                   2                 2   
45          2                   0                   3                 3   
46          2                   0                   4                 4   
47          3                   0                   0                 0   
48          3                   1                   0                 1   
49          3                   2                   0                 2   
50          3                   2                   1                 3   
51          3                   2                   2                 4   
52          3                  